In [4]:
import pandas as pd
import numpy as np
import altair as alt
import os, random
import gensim
import datetime as dt
import altair_saver
from Bio import SeqIO
from Bio.SeqUtils.ProtParam import ProteinAnalysis
from gensim.models import Word2Vec
from sklearn.cluster import KMeans, OPTICS
from sklearn.decomposition import PCA
from sklearn import preprocessing, model_selection, metrics


In [23]:
# Checking if I am using GPU
import tensorflow as tf
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

tf.config.list_physical_devices('GPU') 

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 13088356531004289744
]


[]

## Defining paths for each and every omic

In [6]:
path_root_data = os.path.join ('..', 'Data', 'Extracted', 'Databases')

path_all_fasta = os.path.join (path_root_data, 'fasta_files', 'AllBins')
path_genomics_78 = os.path.join (path_root_data, 'fasta_files', 'rmags_filtered')
path_normalised_metabolomics = os.path.join (path_root_data, 'Metabolomics', 'Normalised_Tables')
path_proteomics_78 = os.path.join (path_root_data, 'Proteomics', 'set_of_78')
path_physico_chemical = os.path.join (path_root_data, 'PhysicoChemical')

path_model_save_root = 'Saved_models'
path_figures_save_root = 'Output_figures'


In [7]:
num_of_mags = len([i for i in os.listdir(path_all_fasta) if (i[-2:] == 'fa')])
num_of_proteomics = len([i for i in os.listdir(path_proteomics_78) if (i[-3:] == 'faa')])
SEED = 42
END = 25
MAX_ROWS = 15000
EPOCHS = 10
NUM_OF_WORKERS = 3
random.seed(SEED)
np.random.seed(SEED)
alt.data_transformers.enable('default', max_rows = MAX_ROWS) # Important if you want to visualize datasets with >5000 samples


DataTransformerRegistry.enable('default')

---
# GENOMIC ANALYSIS
---
## MAG-related functions

**Important**: I should review the way I look at MAGs. The names of all fasta files beggining with 'D_##' represent the days those MAGs were obtained. Therefore, I should look at this also as timeseries data. Also, maybe I should only consider 78 MAGs, and not all ~1300.
After some consideration, I conclude that I should definetly use only 78 MAGs, because that way I wouldn't be tied to meta-omics data only. I also thinked about what should I visualize in that case. One idea is that I should also encode those MAGs with word2wec, and then make a 3D chart where one dimension is time, and other two dimensions would be PCA dimensions of those MAGs. I could also use this function to visualize proteomics data if I want.

Another important thing is that I should actually include FASTA headers and possibly use only them. That way, I could make figures like in a relevant paper where MAGs are groupped according to their taxonomy etc. I should look more into this.

In [8]:
# Function that saves charts from list_of_charts with names from list_of_names
def save_charts (list_of_chart, list_of_names):
    
    for chart, name in zip(list_of_chart, list_of_names):
        altair_saver.save(chart, os.path.join (path_figures_save_root, name))
    

In [9]:
# Function that splits each genome into k-mers thus creating even longer sentence (MAG)
# It returns tokenized genome i.e. [kmer, kmer,...]
def split_genome (genome, k = 5):
    new_genome = []
    n = len(genome)
    
    if n-k <=0:
        return genome
    else:
        for i in range(n-k):
            new_genome.append(genome[i:i+k])
        
        return new_genome


def vectorize_one_mag (one_mag, w2v_model):
    
    # We have to generate vectors for each word in one MAG and then create vector representation of that MAG
    # by averaging vectors of its words
    zero_vector = np.zeros(w2v_model.vector_size)
    word_vectors = []
    one_mag_vector = []
    
    for sentence in one_mag:
        for word in sentence:
            if word in w2v_model.wv:
                try:
                    word_vectors.append(w2v_model.wv[word])
                except KeyError:
                    print ('Key Error')
                    continue
    
    if word_vectors:
        word_vectors = np.asarray(word_vectors)
        one_mag_vector = word_vectors.mean (axis=0)
    
    else:
        one_mag_vector = zero_vector
    
    return one_mag_vector


# Function that vectorizes a MAG (document) with a pretrained word2vec model. It returns vector representation of a given MAG
# Vectorization is done by averaging word (k-mer) vectors for the whole document (MAG)
def vectorize_mags (w2v_model, end = 25):
    
    print ('Vectorizing MAGs')
    
    fasta_files = [i for i in os.listdir(path_all_fasta) if (i[-2:] == 'fa')]
    list_of_mag_vectors = []
    
    # This was done so that I could work with first 'end' FASTA files only. Otherwise, I should just remove: i, and enumerate
    for i, fasta_file_name in enumerate(fasta_files):
        
        if i == end:
            break
        
        else:
            with open(os.path.join(path_all_fasta, fasta_file_name), 'r') as input_file:
                
                one_mag = []
                for fasta_string in SeqIO.parse(input_file, "fasta"):
                    
                    # Get kmers of a genome and create a sentence (list of words)
                    temp_kmers = split_genome (str(fasta_string.seq))
                    
                    # Create a document (list of sentences)
                    one_mag.append(temp_kmers)
                    
                # Vectorizing MAGs one by one
                list_of_mag_vectors.append (vectorize_one_mag (one_mag, w2v_model))
    
    print ('Finished vectorizing')
    
    return list_of_mag_vectors
    
    

# If one wants to import MAGs in order to vectorize them, one should use start argument in order to skip first 'start' MAGs
# If one wants to import MAGs to train word2vec model, one should use only end argument, so that first 'end' MAGs are used for training
# Todo: Implement randomisation in picking MAGs for training, and don't use first 'start' MAGs for training
# (create list of indexes from 0 to 1364, use sklearn split train test, then traverse directory and use only MAGs with indexes in train for training w2v)
def import_mags_and_build_model (end = 25, path_all_fasta = path_all_fasta):
    
    print ('Importing MAGs')
    
    # There are 1364 MAGs enclosed in FASTA files
    # I have to traverse every FASTA file, and in each file every sequence
    
    fasta_files = [i for i in os.listdir(path_all_fasta) if (i.endswith('fa') and i.startswith('D'))]
    fasta_ids = []
    
    # This was done so that I could work with first 100 FASTA files only. Otherwise, I should just remove: i, and enumerate
    for i, fasta_file_name in enumerate(fasta_files):
        
        if i == end:
            break
        
        else:
            with open(os.path.join(path_all_fasta, fasta_file_name), 'r') as input_file:
                
                one_mag = []
                one_mag_ids = []
                for fasta_string in SeqIO.parse(input_file, "fasta"):
                    
                    # Get kmers of a genome and create a sentence (list of words)
                    temp_kmers = split_genome (str(fasta_string.seq))
                    
                    # Create a document (list of sentences)
                    one_mag.append(temp_kmers)
                    # Save FASTA ids for every MAG
                    one_mag_ids.append(str(fasta_string.id))
                    
                # Save list of ids for one MAG in global list
                fasta_ids.append(one_mag_ids)
                
                # If we do not have a model, we build one
                if i == 0:
                    print ('Building w2v model')
                    # We build our model on the first MAG
                    w2v_model = Word2Vec (sentences = one_mag, size = 100, workers = NUM_OF_WORKERS, seed=SEED)
                
                # Else we just expand its vocabulary
                else:
                    # Now we expand our vocabulary
                    w2v_model.build_vocab (one_mag, update = True)
                    
    print ('Finished building')
    
    return w2v_model, fasta_files, fasta_ids


def train_model (w2v_model, epochs, end = 25):
    
    print ('Starting model training')
    
    # There are 1364 MAGs enclosed in FASTA files
    # I have to traverse every FASTA file, and in each file every sequence
    
    fasta_files = [i for i in os.listdir(path_all_fasta) if (i.endswith('fa') and i.startswith('D'))]
    
    # This was done so that I could work with first 100 FASTA files only. Otherwise, I should just remove: i, and enumerate
    for i, fasta_file_name in enumerate(fasta_files):
        
        if i == end:
            break
        
        else:
            with open(os.path.join(path_all_fasta, fasta_file_name), 'r') as input_file:
                
                one_mag = []
                for fasta_string in SeqIO.parse(input_file, "fasta"):
                    
                    # Get kmers of a genome and create a sentence (list of words)
                    temp_kmers = split_genome (str(fasta_string.seq))
                    
                    # Create a document (list of sentences)
                    one_mag.append(temp_kmers)
                    
                
                w2v_model.train (one_mag, total_examples = w2v_model.corpus_count, epochs = epochs)
                    
    print ('Model training finished')
    
    return w2v_model


def visualize_with_pca (data, labels, centers):
    
    pca_model = PCA (n_components = 2, random_state = SEED)
    data_transformed = pca_model.fit_transform (data)
    
    data_transformed = pd.DataFrame (data_transformed)
    data_transformed.columns = ['PC_1', 'PC_2']
    data_transformed['Labels'] = labels
    
    chart_data = alt.Chart(data_transformed).mark_circle(opacity = 1).encode(
        alt.X ('PC_1:Q'),
        alt.Y ('PC_2:Q'),
        alt.Color ('Labels:N', legend = alt.Legend())
    )
    
    # This means we are visualising centroids from k_means (there are less centroids that data points)
    if labels.shape[0] != centers.shape[0]:
        
        centers_transformed = pca_model.fit_transform (centers)
        centers_transformed = pd.DataFrame (centers_transformed)
        centers_transformed.columns = ['PC_1', 'PC_2']
        
        chart_centers = alt.Chart(centers_transformed).mark_point(shape = 'diamond', color = 'black', size = 50, opacity = 0.7).encode(
            alt.X ('PC_1:Q'),
            alt.Y ('PC_2:Q'),
        )
        
        return chart_data + chart_centers
    
    # For DBSCAN there are no centroids
    else:
        return chart_data



## MAG examination

In [10]:
# FOR CLUSTERING I SHOULD CREATE A DATAFRAME WITH MAGs INDEXES AND THEIR VECTOR REPRESENTATIONS
final_model, fasta_names, fasta_ids = import_mags_and_build_model (end = END, path_all_fasta = path_genomics_78)


Importing MAGs
Building w2v model
Finished building


In [11]:


# IT APPEARS THAT I CANNOT USE THIS NAMES, SINCE THEY ARE NOT TIED TO EXACT ORGANISMS. THEREFORE, I WILL ONLY TRY TO CLUSTER THEM


fasta_names

['D42_G14.fa',
 'D05_L3.17.fa',
 'D44_G14.fa',
 'D36_L2.1.6.2.fa',
 'D36_L1.15.fa',
 'D20_O1.13.fa',
 'D12_L1.3.fa',
 'D47_P30.fa',
 'D15_G4.fa',
 'D33_L1.8.2.fa',
 'D37_L8.fa',
 'D32_O1.57.fa',
 'D04_O2.19.fa',
 'D30_O2.4.2.2.2.fa',
 'D20_P23.fa',
 'D51_G1.1.2.fa',
 'D08_P1.44.fa',
 'D37_G1.25.1.fa',
 'D39_O1.57.fa',
 'D23_P13.fa',
 'D04_G2.13.fa',
 'D05_G3.4.fa',
 'D49_G15.fa',
 'D47_O14.fa',
 'D22_G1.42.2.fa',
 'D08_O6.fa',
 'D11_O1.27.3.fa',
 'D35_G2.61.fa',
 'D20_G1.24.fa',
 'D20_O1.17.fa',
 'D46_L2.48.fa',
 'D49_O1.fa',
 'D16_L3.1.1.fa',
 'D31_O1.3.2.fa',
 'D28_L2.9.fa',
 'D15_L1.3.fa',
 'D44_O1.1.2.2.1.2.7.fa',
 'D47_O5.fa',
 'D13_L7.fa',
 'D35_G2.23.fa',
 'D04_L6.fa',
 'D42_G1.1.2.3.fa',
 'D29_L5.fa',
 'D28_O5.fa',
 'D30_P23.fa',
 'D10_O1.45.fa',
 'D26_L1.23.fa',
 'D36_G7.fa',
 'D04_G2.5.fa',
 'D51_G9.fa',
 'D51_L1.24.fa',
 'D22_L1.5.4.fa',
 'D37_G5.fa',
 'D15_O1.7.1.2.1.fa',
 'D05_G3.14.1.fa',
 'D15_G1.8.fa',
 'D19_G1.34.1.1.fa',
 'D36_L1.41.fa',
 'D11_O1.7.fa',
 'D41_O4.fa',


In [12]:
# Train model. It tooks ~10 minutes for END = 25 amount of MAGs
final_model = train_model (final_model, epochs = EPOCHS, end = END)


Starting model training


KeyboardInterrupt: 

In [ ]:
final_model.wv.save_word2vec_format(os.path.join (path_model_save_root, 'model_78.bin'), binary=True) 

Now I should vectorize documents with this model. For further use, I could save this model's weights, and use it to vectorize all mags. That would take a lot, but every MAG will have its vector representation
> This could be done by importing one MAG at a time, then tokenizing it (like before), then getting vector representations of that MAG's sentences (genomes) and then finding the vector representation of the whole MAG (document). If I do that for one MAG at a time, There is no need to worry about memory


In [ ]:
list_of_mag_vectors = vectorize_mags (final_model, end = END)
list_of_mag_vectors[0:2]

In [ ]:
mags_df = pd.DataFrame (list_of_mag_vectors)
mags_df

## Data preprocessing

In [ ]:
mag_scaler = preprocessing.StandardScaler()
scaled_mags_df = mag_scaler.fit_transform(mags_df)
scaled_mags_df

## Clustering

### 1. K-means

In [ ]:
k_range_end = 15 # Usually it is sqrt(# of mags)

k_range = range(1, k_range_end)

k_mean_models = [KMeans (n_clusters = i, random_state = SEED) for i in k_range]
k_scores = [k_mean_model.fit(scaled_mags_df).score(scaled_mags_df) for k_mean_model in k_mean_models]
k_data = pd.DataFrame ({'k_range':k_range, 'k_scores':k_scores})

In [ ]:
k_num_chart = alt.Chart(data = k_data).mark_line().encode(
    alt.X ('k_range:Q'),
    alt.Y ('k_scores:Q')
)

k_num_chart

In [ ]:
# We can see from the chart above that 6 or 7 clusters are optimal for this task (where END = 25 MAGs)
num_of_clusters = 7

k_means_model = KMeans (n_clusters = num_of_clusters, random_state = SEED)
k_means_predicted = k_means_model.fit_predict(scaled_mags_df)
k_means_predicted

In [ ]:
k_means_chart = visualize_with_pca (scaled_mags_df, k_means_predicted, k_means_model.cluster_centers_)
k_means_chart


### 2. OPTICS

In [ ]:
MIN_SAMPLES = 3

optics_model = OPTICS (min_samples = MIN_SAMPLES, n_jobs = NUM_OF_WORKERS)
optics_predicted = optics_model.fit_predict (scaled_mags_df)
optics_predicted

In [ ]:
# Visualize clusters, since there are no centroids, we are sending bogus array
optics_chart = visualize_with_pca (scaled_mags_df, optics_predicted, np.empty([optics_predicted.shape[0], 1], dtype=int))
optics_chart


In [ ]:
# Side by side comparison
alt.hconcat (k_means_chart, optics_chart).resolve_scale(color='independent')

## Evaluation

In [19]:
eval_k_means = metrics.silhouette_score (scaled_mags_df, k_means_predicted)
eval_optics = metrics.silhouette_score (scaled_mags_df, optics_predicted)

print ('Silhouette scores: [best = 1, worst = -1]')
print ('\t1. K-means:', eval_k_means)
print ('\t2. OPTICS:', eval_optics)

Silhouette scores: [best = 1, worst = -1]
	1. K-means: 0.3545105482425982
	2. OPTICS: 0.2898402877092666


---
# METABOLOMIC ANALYSIS
---
## Importing Metabolomic data

In [20]:
metabolomics_file_name = os.path.join(path_normalised_metabolomics, os.listdir(path_normalised_metabolomics)[0])
metabolomics_df = pd.read_csv (metabolomics_file_name, delimiter = '\t')
metabolomics_df

Metabolite   tp        date type known_type     means  \
0      !Phosphoric_acid_3TMS   D1  2012-04-17  snp      known  0.757113   
1      !Phosphoric_acid_3TMS  D10  2012-01-25  snp      known  0.720935   
2      !Phosphoric_acid_3TMS  D11  2012-03-22  snp      known  0.625047   
3      !Phosphoric_acid_3TMS  D12  2012-01-19  snp      known  0.964956   
4      !Phosphoric_acid_3TMS  D13  2011-05-13  snp      known  0.963984   
...                      ...  ...         ...  ...        ...       ...   
18865            Valine_2TMS  D51  2011-08-11   bp      known  0.704821   
18866            Valine_2TMS   D6  2011-06-03   bp      known  1.085888   
18867            Valine_2TMS   D7  2012-04-04   bp      known  2.958023   
18868            Valine_2TMS   D8  2012-02-08   bp      known  2.515980   
18869            Valine_2TMS   D9  2011-12-28   bp      known  2.356989   

        medians       sds  N        se        ci          type2 measurement  \
0      0.737943  0.098650  3  0.056956  4.302653  extracellular    nonpolar   
1      0.873509  0.266593  3  0.153918  4.302653  extracellular    nonpolar   
2      0.652268  0.057820  3  0.033382  4.302653  extracellular    nonpolar   
3      0.941878  0.053754  3  0.031035  4.302653  extracellular    nonpolar   
4      0.974479  0.071659  3  0.041373  4.302653  extracellular    nonpolar   
...         ...       ... ..       ...       ...            ...         ...   
18865  0.478251  0.428368  3  0.247319  4.302653  intracellular       polar   
18866  1.197471  0.487484  3  0.281449  4.302653  intracellular       polar   
18867  2.813145  0.341213  3  0.197000  4.302653  intracellular       polar   
18868  2.322248  0.618556  3  0.357123  4.302653  intracellular       polar   
18869  2.280757  0.264918  3  0.152950  4.302653  intracellular       polar   

           KEGG.Compound.ID                Chebi.Name  \
0                    C00009           phosphoric acid   
1                    C00009           phosphoric acid   
2                    C00009           phosphoric acid   
3                    C00009           phosphoric acid   
4                    C00009           phosphoric acid   
...                     ...                       ...   
18865  C16436,C06417,C00183  valine;D-valine;L-valine   
18866  C16436,C06417,C00183  valine;D-valine;L-valine   
18867  C16436,C06417,C00183  valine;D-valine;L-valine   
18868  C16436,C06417,C00183  valine;D-valine;L-valine   
18869  C16436,C06417,C00183  valine;D-valine;L-valine   

            Chebi.Name_combined  
0               phosphoric acid  
1               phosphoric acid  
2               phosphoric acid  
3               phosphoric acid  
4               phosphoric acid  
...                         ...  
18865  valine;D-valine;L-valine  
18866  valine;D-valine;L-valine  
18867  valine;D-valine;L-valine  
18868  valine;D-valine;L-valine  
18869  valine;D-valine;L-valine  

[18870 rows x 16 columns]

## Data preprocessing

In [21]:
metabolomics_df['date'] = pd.to_datetime(metabolomics_df['date'])
metabolomics_df.insert (0, 'date', metabolomics_df.pop('date'))
metabolomics_df.sort_values ('date', inplace = True, ignore_index = True)
metabolomics_df

date                          Metabolite   tp type known_type  \
0     2011-03-21                        Leucine_2TMS  D37   sp      known   
1     2011-03-21    No match: 1181.78_EM_SP_D1_1_223  D37   sp    unknown   
2     2011-03-21              unknown#emu_WW_2144.25  D37  bnp    unknown   
3     2011-03-21                 Unknown#bth_pae_001  D37   bp    unknown   
4     2011-03-21    No match: 2220.34_EM_BP_D1_1_192  D37   bp    unknown   
...          ...                                 ...  ...  ...        ...   
18865 2012-05-03                    Octadecanol_1TMS  D48  bnp      known   
18866 2012-05-03     No match: 1447.93_EM_BP_D2_1_57  D48   bp    unknown   
18867 2012-05-03                      Lactulose_8TMS  D48   bp      known   
18868 2012-05-03  No match: 2004.78_EM_BNP_D10_1_205  D48  bnp    unknown   
18869 2012-05-03     2-Oxobutanoic_acid_1_1MeOX_1TMS  D48   sp      known   

          means   medians       sds  N        se        ci          type2  \
0      1.440122  1.489979  0.146440  3  0.084547  4.302653  extracellular   
1      3.778469  3.801417  1.924377  3  1.111040  4.302653  extracellular   
2      0.949545  0.947209  0.065422  3  0.037771  4.302653  intracellular   
3      2.095116  1.809891  1.916896  3  1.106721  4.302653  intracellular   
4      1.631643  1.571125  0.168501  3  0.097284  4.302653  intracellular   
...         ...       ...       ... ..       ...       ...            ...   
18865  1.364105  1.457780  0.170311  3  0.098329  4.302653  intracellular   
18866  4.815774  1.160165  6.835474  3  3.946463  4.302653  intracellular   
18867  0.697489  0.684339  0.049632  3  0.028655  4.302653  intracellular   
18868  0.785996  0.744529  0.139901  3  0.080772  4.302653  intracellular   
18869  0.755565  0.709972  0.149214  3  0.086149  4.302653  extracellular   

      measurement      KEGG.Compound.ID                   Chebi.Name  \
0           polar  C16439,C00123,C01570  leucine;L-leucine;D-leucine   
1           polar                   NaN                          NaN   
2        nonpolar                   NaN                          NaN   
3           polar                   NaN                          NaN   
4           polar                   NaN                          NaN   
...           ...                   ...                          ...   
18865    nonpolar                D01924               octadecan-1-ol   
18866       polar                   NaN                          NaN   
18867       polar                C07064                    lactulose   
18868    nonpolar                   NaN                          NaN   
18869       polar                C00109           2-oxobutanoic acid   

               Chebi.Name_combined  
0      leucine;L-leucine;D-leucine  
1                              NaN  
2                              NaN  
3                              NaN  
4                              NaN  
...                            ...  
18865               octadecan-1-ol  
18866                          NaN  
18867                    lactulose  
18868                          NaN  
18869           2-oxobutanoic acid  

[18870 rows x 16 columns]

In [22]:
# Changing metabolite name if it is unknown
metabolomics_df.loc[metabolomics_df['known_type'].eq('unknown'), 'Metabolite'] = np.nan
metabolomics_df

date                       Metabolite   tp type known_type  \
0     2011-03-21                     Leucine_2TMS  D37   sp      known   
1     2011-03-21                              NaN  D37   sp    unknown   
2     2011-03-21                              NaN  D37  bnp    unknown   
3     2011-03-21                              NaN  D37   bp    unknown   
4     2011-03-21                              NaN  D37   bp    unknown   
...          ...                              ...  ...  ...        ...   
18865 2012-05-03                 Octadecanol_1TMS  D48  bnp      known   
18866 2012-05-03                              NaN  D48   bp    unknown   
18867 2012-05-03                   Lactulose_8TMS  D48   bp      known   
18868 2012-05-03                              NaN  D48  bnp    unknown   
18869 2012-05-03  2-Oxobutanoic_acid_1_1MeOX_1TMS  D48   sp      known   

          means   medians       sds  N        se        ci          type2  \
0      1.440122  1.489979  0.146440  3  0.084547  4.302653  extracellular   
1      3.778469  3.801417  1.924377  3  1.111040  4.302653  extracellular   
2      0.949545  0.947209  0.065422  3  0.037771  4.302653  intracellular   
3      2.095116  1.809891  1.916896  3  1.106721  4.302653  intracellular   
4      1.631643  1.571125  0.168501  3  0.097284  4.302653  intracellular   
...         ...       ...       ... ..       ...       ...            ...   
18865  1.364105  1.457780  0.170311  3  0.098329  4.302653  intracellular   
18866  4.815774  1.160165  6.835474  3  3.946463  4.302653  intracellular   
18867  0.697489  0.684339  0.049632  3  0.028655  4.302653  intracellular   
18868  0.785996  0.744529  0.139901  3  0.080772  4.302653  intracellular   
18869  0.755565  0.709972  0.149214  3  0.086149  4.302653  extracellular   

      measurement      KEGG.Compound.ID                   Chebi.Name  \
0           polar  C16439,C00123,C01570  leucine;L-leucine;D-leucine   
1           polar                   NaN                          NaN   
2        nonpolar                   NaN                          NaN   
3           polar                   NaN                          NaN   
4           polar                   NaN                          NaN   
...           ...                   ...                          ...   
18865    nonpolar                D01924               octadecan-1-ol   
18866       polar                   NaN                          NaN   
18867       polar                C07064                    lactulose   
18868    nonpolar                   NaN                          NaN   
18869       polar                C00109           2-oxobutanoic acid   

               Chebi.Name_combined  
0      leucine;L-leucine;D-leucine  
1                              NaN  
2                              NaN  
3                              NaN  
4                              NaN  
...                            ...  
18865               octadecan-1-ol  
18866                          NaN  
18867                    lactulose  
18868                          NaN  
18869           2-oxobutanoic acid  

[18870 rows x 16 columns]

In [23]:
print ('Dataset uniqueness:')
print ('\t1. Timestamps:', len(metabolomics_df['date'].unique()))
print ('\t2. Metabolites:', len(metabolomics_df['Metabolite'].unique()))
print ('\t3. Types:', len(metabolomics_df['type'].unique()))
print ('\t4. Known types:', len(metabolomics_df['known_type'].unique()))
print ('\t5. Ns:', len(metabolomics_df['N'].unique()))
print ('\t6. Type 2s:', len(metabolomics_df['type2'].unique()))
print ('\t7. Measurements:', len(metabolomics_df['measurement'].unique()))

Dataset uniqueness:
	1. Timestamps: 51
	2. Metabolites: 86
	3. Types: 4
	4. Known types: 2
	5. Ns: 2
	6. Type 2s: 2
	7. Measurements: 2


In [24]:
# Saving the name column and removing unnecessairy columns
#metabolite_names = metabolomics_df['Metabolite']
#metabolomics_df.drop(labels = ['Metabolite', 'tp', 'KEGG.Compound.ID', 'Chebi.Name', 'Chebi.Name_combined'], axis = 1, inplace = True)
metabolomics_df.drop(labels = ['tp', 'KEGG.Compound.ID', 'Chebi.Name', 'Chebi.Name_combined'], axis = 1, inplace = True)
metabolomics_df

date                       Metabolite type known_type     means  \
0     2011-03-21                     Leucine_2TMS   sp      known  1.440122   
1     2011-03-21                              NaN   sp    unknown  3.778469   
2     2011-03-21                              NaN  bnp    unknown  0.949545   
3     2011-03-21                              NaN   bp    unknown  2.095116   
4     2011-03-21                              NaN   bp    unknown  1.631643   
...          ...                              ...  ...        ...       ...   
18865 2012-05-03                 Octadecanol_1TMS  bnp      known  1.364105   
18866 2012-05-03                              NaN   bp    unknown  4.815774   
18867 2012-05-03                   Lactulose_8TMS   bp      known  0.697489   
18868 2012-05-03                              NaN  bnp    unknown  0.785996   
18869 2012-05-03  2-Oxobutanoic_acid_1_1MeOX_1TMS   sp      known  0.755565   

        medians       sds  N        se        ci          type2 measurement  
0      1.489979  0.146440  3  0.084547  4.302653  extracellular       polar  
1      3.801417  1.924377  3  1.111040  4.302653  extracellular       polar  
2      0.947209  0.065422  3  0.037771  4.302653  intracellular    nonpolar  
3      1.809891  1.916896  3  1.106721  4.302653  intracellular       polar  
4      1.571125  0.168501  3  0.097284  4.302653  intracellular       polar  
...         ...       ... ..       ...       ...            ...         ...  
18865  1.457780  0.170311  3  0.098329  4.302653  intracellular    nonpolar  
18866  1.160165  6.835474  3  3.946463  4.302653  intracellular       polar  
18867  0.684339  0.049632  3  0.028655  4.302653  intracellular       polar  
18868  0.744529  0.139901  3  0.080772  4.302653  intracellular    nonpolar  
18869  0.709972  0.149214  3  0.086149  4.302653  extracellular       polar  

[18870 rows x 12 columns]

In [25]:
# Dummy eencoding categorical data
scaled_metabolomics_df = pd.get_dummies(metabolomics_df, columns = ['type', 'known_type', 'N', 'type2', 'measurement'])
scaled_metabolomics_df

date                       Metabolite     means   medians  \
0     2011-03-21                     Leucine_2TMS  1.440122  1.489979   
1     2011-03-21                              NaN  3.778469  3.801417   
2     2011-03-21                              NaN  0.949545  0.947209   
3     2011-03-21                              NaN  2.095116  1.809891   
4     2011-03-21                              NaN  1.631643  1.571125   
...          ...                              ...       ...       ...   
18865 2012-05-03                 Octadecanol_1TMS  1.364105  1.457780   
18866 2012-05-03                              NaN  4.815774  1.160165   
18867 2012-05-03                   Lactulose_8TMS  0.697489  0.684339   
18868 2012-05-03                              NaN  0.785996  0.744529   
18869 2012-05-03  2-Oxobutanoic_acid_1_1MeOX_1TMS  0.755565  0.709972   

            sds        se        ci  type_bnp  type_bp  type_snp  type_sp  \
0      0.146440  0.084547  4.302653         0        0         0        1   
1      1.924377  1.111040  4.302653         0        0         0        1   
2      0.065422  0.037771  4.302653         1        0         0        0   
3      1.916896  1.106721  4.302653         0        1         0        0   
4      0.168501  0.097284  4.302653         0        1         0        0   
...         ...       ...       ...       ...      ...       ...      ...   
18865  0.170311  0.098329  4.302653         1        0         0        0   
18866  6.835474  3.946463  4.302653         0        1         0        0   
18867  0.049632  0.028655  4.302653         0        1         0        0   
18868  0.139901  0.080772  4.302653         1        0         0        0   
18869  0.149214  0.086149  4.302653         0        0         0        1   

       known_type_known  known_type_unknown  N_2  N_3  type2_extracellular  \
0                     1                   0    0    1                    1   
1                     0                   1    0    1                    1   
2                     0                   1    0    1                    0   
3                     0                   1    0    1                    0   
4                     0                   1    0    1                    0   
...                 ...                 ...  ...  ...                  ...   
18865                 1                   0    0    1                    0   
18866                 0                   1    0    1                    0   
18867                 1                   0    0    1                    0   
18868                 0                   1    0    1                    0   
18869                 1                   0    0    1                    1   

       type2_intracellular  measurement_nonpolar  measurement_polar  
0                        0                     0                  1  
1                        0                     0                  1  
2                        1                     1                  0  
3                        1                     0                  1  
4                        1                     0                  1  
...                    ...                   ...                ...  
18865                    1                     1                  0  
18866                    1                     0                  1  
18867                    1                     0                  1  
18868                    1                     1                  0  
18869                    0                     0                  1  

[18870 rows x 19 columns]

In [26]:
# Standardizing data
metabolomics_scaler = preprocessing.StandardScaler()
scaled_metabolomics_df[['means', 'medians', 'sds', 'se', 'ci']] = metabolomics_scaler.fit_transform(metabolomics_df[['means', 'medians', 'sds', 'se', 'ci']])

scaled_metabolomics_df

date                       Metabolite     means   medians  \
0     2011-03-21                     Leucine_2TMS -0.145146 -0.094812   
1     2011-03-21                              NaN  0.148026  0.316083   
2     2011-03-21                              NaN -0.206653 -0.191297   
3     2011-03-21                              NaN -0.063026 -0.037942   
4     2011-03-21                              NaN -0.121134 -0.080386   
...          ...                              ...       ...       ...   
18865 2012-05-03                 Octadecanol_1TMS -0.154677 -0.100535   
18866 2012-05-03                              NaN  0.278079 -0.153441   
18867 2012-05-03                   Lactulose_8TMS -0.238254 -0.238027   
18868 2012-05-03                              NaN -0.227158 -0.227327   
18869 2012-05-03  2-Oxobutanoic_acid_1_1MeOX_1TMS -0.230973 -0.233470   

            sds        se        ci  type_bnp  type_bp  type_snp  type_sp  \
0     -0.189837 -0.190047 -0.128175         0        0         0        1   
1     -0.000023 -0.000270 -0.128175         0        0         0        1   
2     -0.198486 -0.198695 -0.128175         1        0         0        0   
3     -0.000822 -0.001068 -0.128175         0        1         0        0   
4     -0.187482 -0.187692 -0.128175         0        1         0        0   
...         ...       ...       ...       ...      ...       ...      ...   
18865 -0.187288 -0.187499 -0.128175         1        0         0        0   
18866  0.524288  0.523941 -0.128175         0        1         0        0   
18867 -0.200172 -0.200380 -0.128175         0        1         0        0   
18868 -0.190535 -0.190745 -0.128175         1        0         0        0   
18869 -0.189541 -0.189751 -0.128175         0        0         0        1   

       known_type_known  known_type_unknown  N_2  N_3  type2_extracellular  \
0                     1                   0    0    1                    1   
1                     0                   1    0    1                    1   
2                     0                   1    0    1                    0   
3                     0                   1    0    1                    0   
4                     0                   1    0    1                    0   
...                 ...                 ...  ...  ...                  ...   
18865                 1                   0    0    1                    0   
18866                 0                   1    0    1                    0   
18867                 1                   0    0    1                    0   
18868                 0                   1    0    1                    0   
18869                 1                   0    0    1                    1   

       type2_intracellular  measurement_nonpolar  measurement_polar  
0                        0                     0                  1  
1                        0                     0                  1  
2                        1                     1                  0  
3                        1                     0                  1  
4                        1                     0                  1  
...                    ...                   ...                ...  
18865                    1                     1                  0  
18866                    1                     0                  1  
18867                    1                     0                  1  
18868                    1                     1                  0  
18869                    0                     0                  1  

[18870 rows x 19 columns]

In [27]:
metabolomics_df.dropna(inplace = True)
metabolomics_df.reset_index(drop=True, inplace=True)
metabolomics_df

date                       Metabolite type known_type     means  \
0    2011-03-21                     Leucine_2TMS   sp      known  1.440122   
1    2011-03-21  Glycerol-3-phosphoric_acid_4TMS   bp      known  1.462276   
2    2011-03-21                  Putrescine_4TMS   bp      known  0.667033   
3    2011-03-21               Glyceric_acid_3TMS   sp      known  1.195441   
4    2011-03-21                     Proline_2TMS   sp      known  1.874113   
...         ...                              ...  ...        ...       ...   
6880 2012-05-03  Glycerol-3-phosphoric_acid_4TMS  bnp      known  0.950065   
6881 2012-05-03        1-Monooleoylglycerol_2TMS  bnp      known  1.300665   
6882 2012-05-03                 Octadecanol_1TMS  bnp      known  1.364105   
6883 2012-05-03                   Lactulose_8TMS   bp      known  0.697489   
6884 2012-05-03  2-Oxobutanoic_acid_1_1MeOX_1TMS   sp      known  0.755565   

       medians       sds  N        se        ci          type2 measurement  
0     1.489979  0.146440  3  0.084547  4.302653  extracellular       polar  
1     1.524821  0.204146  3  0.117864  4.302653  intracellular       polar  
2     0.667946  0.145202  3  0.083832  4.302653  intracellular       polar  
3     1.312780  0.294056  3  0.169774  4.302653  extracellular       polar  
4     2.038239  0.541314  3  0.312528  4.302653  extracellular       polar  
...        ...       ... ..       ...       ...            ...         ...  
6880  0.984881  0.098055  3  0.056612  4.302653  intracellular    nonpolar  
6881  1.342977  0.078951  3  0.045582  4.302653  intracellular    nonpolar  
6882  1.457780  0.170311  3  0.098329  4.302653  intracellular    nonpolar  
6883  0.684339  0.049632  3  0.028655  4.302653  intracellular       polar  
6884  0.709972  0.149214  3  0.086149  4.302653  extracellular       polar  

[6885 rows x 12 columns]

## Time series examination

In [28]:
# This function creates new dataframe with column that represent season according to date
# It also concatenate important types with metabolite names
def season_data (data, temporal_column):
    new_df = data
    new_df['season'] = new_df[temporal_column].dt.month%12 // 3 + 1
    
    #important_types = [metabolite_column] + important_types
    #new_df['new_name'] = df[important_types].agg('\n'.join, axis=1)
    
    return new_df

def visualize_metabolites (data, temporal_column, metabolite_column, type_columns):
    
    data_seasoned = season_data (data, temporal_column)
    
    # Extract columns with float values
    float_columns = []
    
    for i in data_seasoned.columns:
        if data_seasoned[i].dtypes == 'float64' or data_seasoned[i].dtypes == 'float32':
            float_columns.append(i)
    
    # Create repeated chart with varying size encodings
    chart = alt.Chart(data_seasoned).mark_point(opacity = 1).encode(
        alt.X (temporal_column, type = 'temporal', scale = alt.Scale (nice = True)),
        alt.Y (metabolite_column, type = 'nominal'),
        alt.Size (alt.repeat("row"), type = 'quantitative'),
        alt.Color ('season:N', scale = alt.Scale (range = ['blue', 'green', 'orange', 'brown'])),
        alt.Tooltip (type_columns, type = 'nominal')
    ).properties(
        width = 1200
    ).repeat(
        row = float_columns
    ).resolve_scale(color = 'independent', size = 'independent')#.interactive()
    
    return chart


In [29]:
metabolites_chart = visualize_metabolites(metabolomics_df, 'date', 'Metabolite', ['type', 'type2', 'measurement', 'N'])
metabolites_chart

alt.RepeatChart(...)

## Clustering

In [30]:
# Deep learning temporal clustering

# Should I even do this? Previous visualizations are descriptive enough. It would be a lot of work for not much benefit


---
# PROTEOMIC ANALYSIS
---
## Importing Proteomic data

In [31]:
# I could create something similar to Fig. 5 of the original paper, where I would calculate mean of different proteomic feature values for each rMAG calculated by days
# So I would have a table: date | feature 1 | feature 2 | ...
# Where each feature is mean of all values for one day of each MAG in that rMAG

In [32]:
def import_proteomics (end = 25, path_proteomics = path_proteomics_78):
    
    print ('Importing proteomics data')
    
    # There are 78 FASTA files
    # I have to traverse every FASTA file, and in each file every protein sequence
    
    fasta_files = [i for i in os.listdir(path_proteomics) if (i[-3:] == 'faa')]
    tmp_all = []
    
    # This was done so that I could work with first 100 FASTA files only. Otherwise, I should just remove: i, and enumerate
    for i, fasta_file_name in enumerate(fasta_files):
        
        if i == end:
            break
        
        else:
            with open(os.path.join(path_proteomics, fasta_file_name), 'r') as input_file:
                
                one_mag_list = []
                for fasta_string in SeqIO.parse(input_file, "fasta"):
                    
                    # Analyzing protein (peptide) and creating list of values for one MAG
                    sequence = str(fasta_string.seq)
                    
                    if '*' in sequence:
                        continue
                    
                    else:
                    
                        sequence_analysis = ProteinAnalysis (sequence)
                        
                        tmp_list = [sequence_analysis.molecular_weight(), sequence_analysis.gravy(), sequence_analysis.aromaticity(), sequence_analysis.instability_index(), sequence_analysis.isoelectric_point()]
                        
                        tmp_sec_str = sequence_analysis.secondary_structure_fraction()
                        tmp_list += [tmp_sec_str[0], tmp_sec_str[1], tmp_sec_str[2]]
                        tmp_list.append (sequence.count('K') + sequence.count('R') - sequence.count('D') - sequence.count('E')) # Electricity
                        
                        amino_acid_perc = sequence_analysis.get_amino_acids_percent()
                        
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'AGILPV']))
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'STNQ']))
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'QNHSTYCMW']))
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'AGILPVF']))
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'HKR']))
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'CM']))
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'DE']))
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'NQ']))
                        tmp_list.append (sum ([amino_acid_perc[aa] for aa in 'ST']))
                        
                        # Now I put all these values in one_mag_list as a numpy arrays
                        one_mag_list.append(np.asarray(tmp_list))
                        
                # Now I put one mag values, aggregated by mean, into the all mag list
                tmp_all.append (np.asarray(one_mag_list).mean (axis = 0))
    
    
    COLUMN_LIST = ['Molecular weight', 'Gravy', 'Aromaticity', 'Instability index', 'Isoelectric point', 'Secondary structure fraction 0', 'Secondary structure fraction 1', 'Secondary structure fraction 2', 'Electricity', 'Fraction aliphatic', 'Fraction uncharged polar', 'Fraction polar', 'Fraction hydrophobic', 'Fraction positive', 'Fraction sulfur', 'Fraction negative', 'Fraction amide', 'Fraction alcohol']
    all_mag_df = pd.DataFrame (tmp_all, columns = COLUMN_LIST)
    
    print ('Finished importing')
    
    return all_mag_df

def visualize_proteomics (data):
    
    # Adding another column that replaces temporal data for now
    if 'Index_tmp' not in data.columns:
        data.insert (0, 'Index_tmp', data.index.values)
    
    # Create repeated chart
    chart = alt.Chart(data).mark_area().encode(
        alt.X ('Index_tmp', type = 'quantitative'),
        alt.Y (alt.repeat('row'), type = 'quantitative'),
    ).properties(
        width = 1200
    ).repeat(
        row = data.columns.values
    )#.resolve_scale(color = 'independent', size = 'independent')#.interactive()
    
    return chart


In [33]:
proteomics_data = import_proteomics (end = num_of_proteomics)
proteomics_data

Importing proteomics data
Finished importing


Molecular weight     Gravy  Aromaticity  Instability index  \
0       30107.370303 -0.029115     0.069055          39.655099   
1       31945.929807 -0.157285     0.104198          34.785878   
2       33336.676155 -0.045767     0.059752          37.570359   
3       26058.479897 -0.104694     0.072250          39.041305   
4       27971.040966 -0.232816     0.101992          33.917894   
..               ...       ...          ...                ...   
73      24586.140194 -0.113981     0.060095          39.992533   
74      33364.056584 -0.161289     0.100820          33.432398   
75      26741.991077 -0.108067     0.073667          37.581279   
76      34303.306631  0.032637     0.059614          35.771707   
77      23394.926871 -0.179135     0.098395          35.598115   

    Isoelectric point  Secondary structure fraction 0  \
0            7.354626                        0.305178   
1            7.207581                        0.344477   
2            6.049116                        0.285099   
3            7.346492                        0.303804   
4            7.294352                        0.347434   
..                ...                             ...   
73           6.646171                        0.279006   
74           7.590524                        0.332487   
75           7.504971                        0.296754   
76           6.769888                        0.290662   
77           7.604109                        0.340443   

    Secondary structure fraction 1  Secondary structure fraction 2  \
0                         0.210988                        0.303285   
1                         0.222770                        0.243080   
2                         0.230651                        0.306529   
3                         0.205971                        0.294666   
4                         0.220156                        0.240268   
..                             ...                             ...   
73                        0.234656                        0.280482   
74                        0.218691                        0.250484   
75                        0.221329                        0.286249   
76                        0.225830                        0.310594   
77                        0.212586                        0.253027   

    Electricity  Fraction aliphatic  Fraction uncharged polar  Fraction polar  \
0     -1.273648            0.497255                  0.173165        0.269161   
1     -0.647059            0.399968                  0.210687        0.318818   
2    -10.212190            0.506151                  0.164821        0.247837   
3     -0.469168            0.461895                  0.187834        0.289298   
4      0.034398            0.379836                  0.223348        0.317693   
..          ...                 ...                       ...             ...   
73    -4.912468            0.477694                  0.180007        0.270632   
74     1.369316            0.407491                  0.207281        0.314093   
75    -1.240703            0.469162                  0.169856        0.278743   
76    -4.963504            0.521625                  0.160698        0.242854   
77     1.418097            0.390472                  0.203381        0.294227   

    Fraction hydrophobic  Fraction positive  Fraction sulfur  \
0               0.529845           0.126935         0.032892   
1               0.453415           0.134969         0.037200   
2               0.533880           0.114913         0.029888   
3               0.500347           0.134007         0.040014   
4               0.435946           0.143279         0.031380   
..                   ...                ...              ...   
73              0.508087           0.127144         0.036477   
74              0.458395           0.136934         0.038155   
75              0.504968           0.140227         0.041462   
76              0.549332           0.119270         0.028500   
77      

In [34]:
chart_proteomics = visualize_proteomics(proteomics_data)
chart_proteomics

alt.RepeatChart(...)

---
# PHYSICO-CHEMICAL ANALYSIS
---
## Importing Physico-chemical data

In [35]:
phy_che_file_name = os.path.join(path_physico_chemical, [i for i in os.listdir(path_physico_chemical) if (i.endswith(('.tsv', '.csv')))][1])
phy_che_df = pd.read_csv (phy_che_file_name, decimal = ',')
phy_che_df

/home/alexein/miniconda3/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (24,27,28) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


Date  Time Inflow_Volume Inflow_pH Inflow_conductivity      T  \
0           NaN   NaN          m3/h        pH               µS/cm      C   
1      07/03/02   1.0        437.13      8.55                5.10  43.80   
2      07/03/02   3.0        308.08      8.52                5.15  46.92   
3      07/03/02   5.0        255.27      8.49                5.30  49.24   
4      07/03/02   7.0        261.22      8.42                5.36  39.20   
...         ...   ...           ...       ...                 ...    ...   
61138  11/19/18  15.0        599.03      8.09             1615.81  16.29   
61139  11/19/18  17.0        579.19      7.97             1574.42  16.34   
61140  11/19/18  19.0        696.77      7.88             1476.28  15.96   
61141  11/19/18  21.0        942.94      7.83             1366.18  15.45   
61142  11/19/18  23.0        951.35      7.97             1317.89  15.41   

      outf_preclarifier_volume outf_preclarifier_COD outf_preclarifier_NH4-N  \
0                         m3/h                  mg/l                    mg/l   
1                       0.0956                334.13                    0.00   
2                       0.0166                331.81                    0.00   
3                       0.0258                319.13                    0.00   
4                       0.0916                303.37                    0.00   
...                        ...                   ...                     ...   
61138                 144.8233                195.59                   80.00   
61139                 147.6642                300.74                   80.00   
61140                 148.2223                469.70                   80.00   
61141                 150.4223                384.14                   70.51   
61142                 149.5530                302.57                   49.01   

      Abschlagmenge_Durchfluß  ... Rücklaufschlamm Überfallmenge1_Durchfluß  \
0                        m3/h  ...            m3/h                     m3/h   
1                        7.11  ...         1365.87                      778   
2                        4.13  ...         1362.75                      773   
3                        5.74  ...         1359.20                      772   
4                        5.33  ...         1355.74                      770   
...                       ...  ...             ...                      ...   
61138                    6.14  ...          534.42                      287   
61139                    5.57  ...          488.12                      268   
61140                    4.99  ...          575.44                      309   
61141                    3.77  ...          900.10                      478   
61142                    3.17  ...          946.16                      500   

      Überfallmenge2_Durchfluß Rücklaufschlamm_TS Menge_Ablauf_Durchfluß  \
0                         m3/h                g/l                   m3/h   
1                          754              10.94                   0.00   
2                          718              10.40                   0.00   
3                          707               9.84                   0.00   
4                          709               9.63                   0.00   
...                        ...                ...                    ...   
61138                      286               8.81                 440.26   
61139                      270               9.17                 410.50   
61140                      311               8.58                 482.34   
61141                      477               5.75                 739.48   
61142                      501               6.10                 767.37   

      Outflow_pH Outflow_Conductivity Menge_Fäkalien_Durchfluß  \
0             pH                mS/cm                     m3/h   
1           2.00                 0.00                   0.0000   
2           2.00                 0.00                   0.0000   
3          

## Data preprocessing

In [36]:
phy_che_df.drop(index = 0, axis = 1, inplace = True)
phy_che_df['Date'] = pd.to_datetime(phy_che_df['Date'])
phy_che_df['Time'] = pd.to_timedelta(phy_che_df["Time"], unit = 'h')
phy_che_df

Date            Time Inflow_Volume Inflow_pH Inflow_conductivity  \
1     2002-07-03 0 days 01:00:00        437.13      8.55                5.10   
2     2002-07-03 0 days 03:00:00        308.08      8.52                5.15   
3     2002-07-03 0 days 05:00:00        255.27      8.49                5.30   
4     2002-07-03 0 days 07:00:00        261.22      8.42                5.36   
5     2002-07-03 0 days 09:00:00        439.54      8.53                6.24   
...          ...             ...           ...       ...                 ...   
61138 2018-11-19 0 days 15:00:00        599.03      8.09             1615.81   
61139 2018-11-19 0 days 17:00:00        579.19      7.97             1574.42   
61140 2018-11-19 0 days 19:00:00        696.77      7.88             1476.28   
61141 2018-11-19 0 days 21:00:00        942.94      7.83             1366.18   
61142 2018-11-19 0 days 23:00:00        951.35      7.97             1317.89   

           T outf_preclarifier_volume outf_preclarifier_COD  \
1      43.80                   0.0956                334.13   
2      46.92                   0.0166                331.81   
3      49.24                   0.0258                319.13   
4      39.20                   0.0916                303.37   
5      40.48                   0.0895                288.80   
...      ...                      ...                   ...   
61138  16.29                 144.8233                195.59   
61139  16.34                 147.6642                300.74   
61140  15.96                 148.2223                469.70   
61141  15.45                 150.4223                384.14   
61142  15.41                 149.5530                302.57   

      outf_preclarifier_NH4-N Abschlagmenge_Durchfluß  ... Rücklaufschlamm  \
1                        0.00                    7.11  ...         1365.87   
2                        0.00                    4.13  ...         1362.75   
3                        0.00                    5.74  ...         1359.20   
4                        0.00                    5.33  ...         1355.74   
5                        0.00                    4.93  ...         1349.17   
...                       ...                     ...  ...             ...   
61138                   80.00                    6.14  ...          534.42   
61139                   80.00                    5.57  ...          488.12   
61140                   80.00                    4.99  ...          575.44   
61141                   70.51                    3.77  ...          900.10   
61142                   49.01                    3.17  ...          946.16   

      Überfallmenge1_Durchfluß Überfallmenge2_Durchfluß Rücklaufschlamm_TS  \
1                          778                      754              10.94   
2                          773                      718              10.40   
3                          772                      707               9.84   
4                          770                      709               9.63   
5                          774                      709               9.81   
...                        ...                      ...                ...   
61138                      287                      286               8.81   
61139                      268                      270               9.17   
61140                      309                      311               8.58   
61141                      478                      477               5.75   
61142                      500                      501               6.10   

      Menge_Ablauf_Durchfluß Outflow_pH Outflow_Conductivity  \
1                       0.00       2.00                 0.00   
2                       0.00       2.00                 0.00   
3                       0.00       2.00                 0.00   
4                       0.00       2.00                 0.00   
5                       0.00       2.00                 0.00   
...                      ...        

In [37]:
filtered_phy_che_df = phy_che_df[(phy_che_df['Date'] >= '2011-03-21') & (phy_che_df['Date'] <= '2012-05-03')]
tmp_column = pd.Series(filtered_phy_che_df['Date'] + filtered_phy_che_df['Time'])

filtered_phy_che_df.drop (['Date', 'Time'], axis = 1, inplace = True)
filtered_phy_che_df.reset_index(inplace = True, drop = True)
filtered_phy_che_df = filtered_phy_che_df.apply(lambda x: pd.to_numeric(x.astype(str).str.replace(',','.')))#, errors='coerce'))
filtered_phy_che_df.insert (0, 'DateTime', tmp_column.values)
filtered_phy_che_df

/home/alexein/miniconda3/lib/python3.8/site-packages/pandas/core/frame.py:4308: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().drop(


DateTime  Inflow_Volume  Inflow_pH  Inflow_conductivity  \
0    2011-03-21 01:00:00         587.82       6.38              2150.46   
1    2011-03-21 03:00:00         492.41       6.33              2215.49   
2    2011-03-21 05:00:00         454.61       6.29              2212.68   
3    2011-03-21 07:00:00         505.10       6.34              2212.21   
4    2011-03-21 09:00:00         610.22       6.20              2205.67   
...                  ...            ...        ...                  ...   
4819 2012-05-03 15:00:00        1236.79       8.57              1094.55   
4820 2012-05-03 17:00:00        1286.00       8.40              1001.93   
4821 2012-05-03 19:00:00        1297.70       8.39               997.82   
4822 2012-05-03 21:00:00        1296.84       8.45              1044.01   
4823 2012-05-03 23:00:00        1297.52       8.39               994.89   

          T  outf_preclarifier_volume  outf_preclarifier_COD  \
0     15.09                    0.0046                 951.78   
1     14.76                    0.0042                 937.98   
2     14.51                    0.0083                 930.48   
3     14.39                    0.0042                 924.90   
4     14.56                   12.2000                 916.73   
...     ...                       ...                    ...   
4819  17.60                    4.9685                 225.49   
4820  17.50                    0.0020                  70.78   
4821  17.39                    0.0037                  58.38   
4822  17.69                    0.0029                  61.13   
4823  17.58                    0.0034                  59.20   

      outf_preclarifier_NH4-N  Abschlagmenge_Durchfluß  \
0                       39.74                     3.64   
1                       42.32                     3.92   
2                       41.47                     3.79   
3                       39.83                     3.75   
4                       28.85                     2.54   
...                       ...                      ...   
4819                    39.17                     1.22   
4820                    23.17                     1.05   
4821                    21.00                     1.03   
4822                    22.61                     1.16   
4823                    23.06                     1.16   

      Stapelbehälter_Durchfluß  ...  Rücklaufschlamm  \
0                       156.79  ...           916.98   
1                       158.46  ...           840.24   
2                       159.22  ...           799.92   
3                       158.51  ...           768.65   
4                         0.22  ...           863.17   
...                        ...  ...              ...   
4819                      0.00  ...          1651.32   
4820                      0.00  ...          1694.97   
4821                      0.00  ...          1749.27   
4822                      0.00  ...          1750.20   
4823                      0.00  ...          1750.38   

      Überfallmenge1_Durchfluß  Überfallmenge2_Durchfluß  Rücklaufschlamm_TS  \
0                        432.0                     431.0                4.93   
1                        374.0                     373.0                5.06   
2                        348.0                     348.0                5.04   
3                        342.0                     342.0                5.08   
4                        415.0                     417.0                4.98   
...                        ...                       ...                 ...   
4819                     894.0                     894.0                8.51   
4820                     915.0                     915.0                8.42   
4821                     950.0                     950.0                8.37   
4822                     952.0                     950.0                8.32   
4823                     955.0                     955.0                8.28   

      Menge_Abl

In [38]:
# Visualize temperature, air_temperature, conductivity, inflow_pH, nitrate, oxygen, pH

def visualize_psy_che (data, temporal_column, list_of_columns):
    
    # Create repeated chart
    chart = alt.Chart(data).mark_line().encode(
        alt.X (temporal_column, type = 'temporal'),#, timeUnit = 'month'),
        alt.Y (alt.repeat('row'), type = 'quantitative'),
    ).properties(
        width = 1200
    ).repeat(
        row = list_of_columns
    )#.resolve_scale(color = 'independent', size = 'independent')#.interactive()
    
    return chart

def visualize_psy_che_heatmap (data):
    
    new_data = data.drop('DateTime', axis = 1)
    corr = new_data.corr().reset_index().melt('index')
    corr.columns = ['var_1', 'var_2', 'correlation']
    
    # Create correlation chart
    chart = alt.Chart(corr).mark_rect().encode(
        alt.X ('var_1', title = None, axis = alt.Axis(labelAngle = -45)),
        alt.Y ('var_2', title = None),
        alt.Color('correlation', legend=None, scale = alt.Scale(scheme='redblue', reverse = True)),
    ).properties(
        width = alt.Step(40),
        height = alt.Step(40)
    )
    
    chart += chart.mark_text(size = 12).encode(
        alt.Text ('correlation', format=".2f"),
        color = alt.condition("abs(datum.correlation) > 0.5", alt.value('white'), alt.value('black'))
    )
    
    return chart.transform_filter("datum.var_1 < datum.var_2") # This returns only lower triangle


In [39]:
chart_psy_che = visualize_psy_che (filtered_phy_che_df, 'DateTime', filtered_phy_che_df.columns.values[4:])
chart_psy_che_corr = visualize_psy_che_heatmap (filtered_phy_che_df)
chart_psy_che_corr

alt.LayerChart(...)

In [40]:
chart_psy_che

alt.RepeatChart(...)